In [1]:
import pandas as pd
import folium
from folium.plugins import MarkerCluster
import plotly.express as px
from IPython.display import display

In [2]:
city_df = pd.read_parquet('../data/processed/city_golf_metrics.parquet')
# load user-provided city coordinates (e.g., data/uscities.csv)
city_coords = pd.read_csv('../data/uscities.csv')
# normalize coordinate column names if needed
if 'lng' in city_coords.columns and 'lat' in city_coords.columns:
    city_coords = city_coords.rename(columns={'lng': 'lon', 'lat': 'lat'})
if 'state_id' in city_coords.columns and 'state' not in city_coords.columns:
    city_coords = city_coords.rename(columns={'state_name': 'state'})
# merge on city + state
merge_cols = ['city','state']
coords_use = [c for c in ['city','state','lat','lon'] if c in city_coords.columns]
city_df = city_df.merge(city_coords[coords_use].drop_duplicates(), how='left', on=['city','state'])
# standardize column names
city_df = city_df.sort_values('num_golf_courses', ascending=False)
city_df_cleaned = city_df.dropna(subset=["lat","lon"]).reset_index(drop=True) 
city_df_cleaned.describe()


num_golf_courses   avg_rating  sum_ratings_count  avg_length_yards  \
count       4571.000000  4571.000000        4571.000000       4293.000000   
mean           1.998687     4.150477         389.921461       5485.365362   
std            2.531638     0.513101        1419.766960       1772.750268   
min            1.000000     3.000000           1.000000          0.000000   
25%            1.000000     3.860000           3.000000       4640.700000   
50%            1.000000     4.130000          33.000000       6300.000000   
75%            2.000000     4.500000         275.000000       6691.000000   
max           49.000000     5.000000       29150.000000      10077.000000   

       state_golfable        score         rank          lat          lon  
count          4571.0  4571.000000  4571.000000  4571.000000  4571.000000  
mean              0.0     0.259832  2809.098447    38.936494   -91.534165  
std               0.0     0.114452  1604.167375     5.052663    14.755054  
min               0.0     0.000000     1.000000    18.333100  -159.480100  
25%               0.0     0.197005  1431.500000    35.441050   -96.914850  
50%               0.0     0.260909  2787.000000    39.889000   -87.703500  
75%               0.0     0.341840  4205.000000    42.245900   -81.440450  
max               0.0     0.718229  5585.000000    64.835300   -65.658900

In [ ]:
center_lat = city_df_cleaned['lat'].mean()
center_lon = city_df_cleaned['lon'].mean()
m = folium.Map(location=[center_lat, center_lon], zoom_start=5, tiles='CartoDB positron')
mc = MarkerCluster().add_to(m)
# compute rating min/max for normalization
min_rating = city_df_cleaned['avg_rating'].min() if 'avg_rating' in city_df_cleaned.columns else None
max_rating = city_df_cleaned['avg_rating'].max() if 'avg_rating' in city_df_cleaned.columns else None
for _, r in city_df_cleaned.iterrows():
    popup = folium.Popup(f"<b>{r['city']}, {r.get('state','')}</b><br/>Courses: {r['num_golf_courses']}<br/>Avg rating: {r.get('avg_rating', 'n/a')}", max_width=300)
    # radius larger for higher average rating (normalized)
    if pd.notna(r.get('avg_rating')) and min_rating is not None and max_rating is not None and max_rating>min_rating:
        norm = (r['avg_rating'] - min_rating) / (max_rating - min_rating + 1e-9)
        radius = 4 + norm * 20  # range approx 4-24
        if r['avg_rating'] >= 4.0:
            color = 'darkgreen'
        elif r['avg_rating'] >= 3.5:
            color = 'orange'
        else:
            color = 'red'
    else:
        # fallback: size by number of courses
        radius = 4 + (r['num_golf_courses']**0.5)
        color = 'blue'
    folium.CircleMarker(location=[r['lat'], r['lon']], radius=radius, color=color, fill=True, fill_opacity=0.7, popup=popup).add_to(mc)

display(m)

True

In [35]:
from folium.plugins import HeatMap
heat_df = city_df.dropna(subset=['lat','lon']).copy()
if heat_df.empty:
    print('No centroids available for heatmaps (no lat/lon in city data).')
else:
    # --- Density heatmap (weight = number of golf courses in city) ---
    vals = heat_df['num_golf_courses'].fillna(0).astype(float)
    if vals.max() == vals.min():
        weights = [1.0] * len(vals)
    else:
        weights = ((vals - vals.min()) / (vals.max() - vals.min())).tolist()
    density_data = [[r['lat'], r['lon'], float(w)] for r, w in zip(heat_df.to_dict('records'), weights)]
    hm_density = folium.Map(location=[heat_df['lat'].mean(), heat_df['lon'].mean()], zoom_start=5, tiles='CartoDB positron')
    HeatMap(density_data, radius=25, blur=10, max_zoom=6).add_to(hm_density)
    folium.LayerControl().add_to(hm_density)
    display(hm_density)

    # --- Rating heatmap (weight = avg_rating normalized) ---
    if 'avg_rating' in heat_df.columns:
        vals = heat_df['avg_rating'].fillna(0).astype(float)
        if vals.max() == vals.min():
            weights = [1.0] * len(vals)
        else:
            weights = ((vals - vals.min()) / (vals.max() - vals.min())).tolist()
        rating_data = [[r['lat'], r['lon'], float(w)] for r, w in zip(heat_df.to_dict('records'), weights)]
        hm_rating = folium.Map(location=[heat_df['lat'].mean(), heat_df['lon'].mean()], zoom_start=5, tiles='CartoDB positron')
        HeatMap(rating_data, radius=25, blur=10, max_zoom=6).add_to(hm_rating)
        folium.LayerControl().add_to(hm_rating)
        display(hm_rating)
    else:
        print('No avg_rating available for rating heatmap.')

In [32]:
#(Re)load courses and import compute_metrics from the script
import importlib.util
from pathlib import Path
spec = importlib.util.spec_from_file_location("compute_city_metrics", str(Path('..') / 'eda' / 'compute_city_metrics.py'))
compute_mod = importlib.util.module_from_spec(spec)
spec.loader.exec_module(compute_mod)
compute_metrics = compute_mod.compute_metrics

courses = pd.read_parquet('../data/processed/teeradar_courses.parquet')

# compute without state_golfable
scores_no_state = compute_metrics(courses, weights=None, state_golfable_csv=None)
# compute with state_golfable
scores_with_state = compute_metrics(courses, weights=None, state_golfable_csv='../data/state_golfable_year_round.csv')
print('Top cities (including state_golfable)')
display(scores_with_state.head(20))
print('\nTop cities (excluding state_golfable)')
display(scores_no_state.head(20))

Top cities (including state_golfable)


city           state  num_golf_courses  avg_rating  \
0           Scottsdale         Arizona                50        3.13   
1              Phoenix         Arizona                31        3.26   
2              Orlando         Florida                69        1.88   
3            Las Vegas          Nevada                38        3.59   
4               Naples         Florida                75        3.03   
5                 Mesa         Arizona                30        3.10   
6               Tucson         Arizona                37        3.20   
7            Bradenton         Florida                26        3.24   
8   Hilton Head Island  South Carolina                22        4.07   
9            Kissimmee         Florida                16        3.52   
10         Palm Desert      California                31        2.89   
11              Austin           Texas                31        3.74   
12            Bluffton  South Carolina                19        3.46   
13          Fort Myers         Florida                37        3.22   
14            Sarasota         Florida                24        3.46   
15            Sun City         Arizona                12        3.73   
16           La Quinta      California                19        3.52   
17        Green Valley         Arizona                 9        4.00   
18             Buckeye         Arizona                 4        4.34   
19               Miami         Florida                22        3.73   

    sum_ratings_count  avg_length_yards  state_golfable     score  rank  
0               27769            6449.9               0  0.540987     1  
1               30589            5712.4               0  0.534208     2  
2               31232            6392.4               0  0.519646     3  
3               23882            6445.9               0  0.517477     4  
4               18858            6422.2               0  0.513255     5  
5               24988            4755.6               0  0.475504     6  
6               21266            5461.6               0  0.467535     7  
7               20965            5877.3               0  0.445586     8  
8               14272            6400.9               0  0.441644     9  
9               17982            5626.8               0  0.420885    10  
10              18111            5268.3               0  0.408219    11  
11               6562            5583.8               0  0.375169    12  
12              11585            5909.5               0  0.371674    13  
13               8847            5710.1               0  0.369460    14  
14               9780            5112.5               0  0.367337    15  
15              10045            5562.1               0  0.363982    16  
16               9860            6820.9               0  0.361791    17  
17               8209            6746.1               0  0.361617    18  
18               6347            7067.0               0  0.360981    19  
19               6821            6196.9               0  0.358192    20


Top cities (excluding state_golfable)


city           state  num_golf_courses  avg_rating  \
0           Scottsdale         Arizona                50        3.13   
1               Naples         Florida                75        3.03   
2              Orlando         Florida                69        1.88   
3              Phoenix         Arizona                31        3.26   
4            Las Vegas          Nevada                38        3.59   
5                 Mesa         Arizona                30        3.10   
6               Tucson         Arizona                37        3.20   
7            Bradenton         Florida                26        3.24   
8   Hilton Head Island  South Carolina                22        4.07   
9            Kissimmee         Florida                16        3.52   
10         Palm Desert      California                31        2.89   
11              Austin           Texas                31        3.74   
12          Fort Myers         Florida                37        3.22   
13            Bluffton  South Carolina                19        3.46   
14            Sarasota         Florida                24        3.46   
15           La Quinta      California                19        3.52   
16               Miami         Florida                22        3.73   
17            Sun City         Arizona                12        3.73   
18        Green Valley         Arizona                 9        4.00   
19         San Antonio           Texas                32        3.20   

    sum_ratings_count  avg_length_yards     score  rank  
0               27769            6449.9  0.714340     1  
1               18858            6422.2  0.704103     2  
2               31232            6392.4  0.699197     3  
3               30589            5712.4  0.689018     4  
4               23882            6445.9  0.677514     5  
5               24988            4755.6  0.616612     6  
6               21266            5461.6  0.614324     7  
7               20965            5877.3  0.577817     8  
8               14272            6400.9  0.574252     9  
9               17982            5626.8  0.540383    10  
10              18111            5268.3  0.535593    11  
11               6562            5583.8  0.501024    12  
12               8847            5710.1  0.496750    13  
13              11585            5909.5  0.483817    14  
14               9780            5112.5  0.483340    15  
15               9860            6820.9  0.472294    16  
16               6821            6196.9  0.472069    17  
17              10045            5562.1  0.469579    18  
18               8209            6746.1  0.465481    19  
19               7234            5915.5  0.462281    20

In [33]:
# Cell 6: Plotly bar charts (top 20) - with state_golfable
top_n = 20
with_state_top = scores_with_state.head(top_n).sort_values('score')
fig1 = px.bar(with_state_top, x='score', y='city', orientation='h', color='state_golfable' if 'state_golfable' in with_state_top.columns else None, title='Top cities (score includes state_golfable)')
fig1.update_layout(height=700, yaxis={'categoryorder':'total ascending'})
fig1.show()

# without state_golfable
without_state_top = scores_no_state.head(top_n).sort_values('score')
fig2 = px.bar(without_state_top, x='score', y='city', orientation='h', title='Top cities (no state_golfable)')
fig2.update_layout(height=700, yaxis={'categoryorder':'total ascending'})
fig2.show()

In [34]:
merged = scores_with_state[['city','state','rank','score']].merge(scores_no_state[['city','state','rank','score']], on=['city','state'], suffixes=('_with','_without'))
merged['rank_change'] = merged['rank_without'] - merged['rank_with']
merged = merged.sort_values('rank_change', key=lambda s: s.abs(), ascending=False).head(20)

from IPython.display import display
print('Cities with largest rank change (top 20)')
display(merged[['city','state','rank_with','rank_without','rank_change','score_with','score_without']])

Cities with largest rank change (top 20)


city                  state  rank_with  rank_without  \
8201           Yoakum                  Texas       8202          6280   
6282  Carrizo Springs                  Texas       6283          8195   
8194     Wrightsville                Georgia       8195          6283   
8193           Wymore               Nebraska       8194          6284   
8192          Wyoming                   Iowa       8193          6285   
8184        Abbeville         South Carolina       8185          6287   
6303      Carlinville               Illinois       6304          8197   
6302         Carlisle  Armed Forces Americas       6303          8196   
6304          Caribou                  Maine       6305          8198   
6305            Carey                   Ohio       6306          8199   
8206         Aberdeen             Washington       8207          6318   
8203         Yemassee         South Carolina       8204          6319   
8199         Ackerman            Mississippi       8200          6317   
8179          Zebulon                Georgia       8180          6298   
8180           Zapata                  Texas       8181          6299   
8165       Woonsocket           South Dakota       8166          6289   
8167         Woodward                   Iowa       8168          6300   
8181           Adrian              Minnesota       8182          6316   
8075           Hersey               Michigan       8076          6304   
8044        Hillsboro                 Kansas       8045          6305   

      rank_change  score_with  score_without  
8201        -1922         0.0            0.0  
6282         1912         0.0            0.0  
8194        -1912         0.0            0.0  
8193        -1910         0.0            0.0  
8192        -1908         0.0            0.0  
8184        -1898         0.0            0.0  
6303         1893         0.0            0.0  
6302         1893         0.0            0.0  
6304         1893         0.0            0.0  
6305         1893         0.0            0.0  
8206        -1889         0.0            0.0  
8203        -1885         0.0            0.0  
8199        -1883         0.0            0.0  
8179        -1882         0.0            0.0  
8180        -1882         0.0            0.0  
8165        -1877         0.0            0.0  
8167        -1868         0.0            0.0  
8181        -1866         0.0            0.0  
8075        -1772         0.0            0.0  
8044        -1740         0.0            0.0